# Capstone Data Acquisition

In [1]:
import json
import requests
import pandas as pd
import numpy as np
import time
import threading
import seaborn as sns
import re

Source for yugioh data: https://db.ygoprodeck.com/api-guide/ this includes the limits on how much and now often pulls can be made as well as explanations for the vast majority of the data on offer.

## Testing the API

In [ ]:
r = requests.get('https://db.ygoprodeck.com/api/v7/cardsets.php')

card_sets = r.json()

#having access to a list of every set of cards in the game may be useful later in the project and this let's us easily 
#access all that data

In [ ]:
print(card_sets[0])
print(len(card_sets))

#here we can see the data returned and decide what we want to keep by looking at a singular entry

In [ ]:
#now we can build a dataframe from our data above that will be useful later, release dates was raising an error initially
#so now I have applied a try except statement to it that means we will likely have to deal with missing data somewhere

SetNames = []
SetCodes = []
TotalCards = []
ReleaseDates = []

for i in card_sets:
    SetNames.append(i['set_name'])
    SetCodes.append(i['set_code'])
    TotalCards.append(i['num_of_cards'])
    try:
        ReleaseDates.append(i['tcg_date'])
    except:
        ReleaseDates.append(None)
    
ygo_sets = pd.DataFrame({'set_names':SetNames,
                        'set_codes':SetCodes,
                        'total_cards':TotalCards,
                        'release_date':ReleaseDates})

In [ ]:
ygo_sets.info()

#we should check the state of the dataframe we have created and handle any missing values

In [ ]:
ygo_sets[ygo_sets.release_date.isnull()]

#here we can see our three missing release dates
#looking up the sets online suggests that the values should be 07/11/2021, 01/01/2021, 01/01/2022 respectively

In [ ]:
ygo_sets.at[50,'release_date'] = '2021-11-07'
ygo_sets.at[687,'release_date'] = '2021-01-01'
ygo_sets.at[688,'release_date'] = '2022-01-01'

#this sets the value at each missing entry to what it should be, while also keeping the same date format as the rest of the
#dataframe

In [ ]:
#for now let's save this data as a csv for future use

ygo_sets.to_csv("ygo_sets.csv", index=False, encoding='utf-8')

In [2]:
#testing another slice of data we can obtain that lists every archetype in the game, this may also be useful later but is
#so straightforward that there is no need to save it right now

r = requests.get('https://db.ygoprodeck.com/api/v7/archetypes.php')

arch = r.json()

In [3]:
print(arch)

#examining the pulled data

[{'archetype_name': '@Ignister'}, {'archetype_name': 'A.I.'}, {'archetype_name': 'ABC'}, {'archetype_name': 'Abhyss'}, {'archetype_name': 'Abyss Actor'}, {'archetype_name': 'Adamancipator'}, {'archetype_name': 'Aesir'}, {'archetype_name': 'Aether'}, {'archetype_name': 'Albaz Dragon'}, {'archetype_name': 'Alien'}, {'archetype_name': 'Alligator'}, {'archetype_name': 'Allure Queen'}, {'archetype_name': 'Ally of Justice'}, {'archetype_name': 'Altergeist'}, {'archetype_name': 'Amazement'}, {'archetype_name': 'Amazoness'}, {'archetype_name': 'Amorphage'}, {'archetype_name': 'Ancient Gear'}, {'archetype_name': 'Ancient Warriors'}, {'archetype_name': 'Angel'}, {'archetype_name': 'Anti'}, {'archetype_name': 'Apoqliphort'}, {'archetype_name': 'Appliancer'}, {'archetype_name': 'Aquaactress'}, {'archetype_name': 'Arcana Force'}, {'archetype_name': 'Archfiend'}, {'archetype_name': 'Armed Dragon'}, {'archetype_name': 'Aroma'}, {'archetype_name': 'Artifact'}, {'archetype_name': 'Assault Mode'}, {'arc

## Pulling the Actual Data and Constucting the Dataset

In [16]:
r = requests.get('https://db.ygoprodeck.com/api/v7/cardinfo.php?misc=yes')

cards = r.json()

#this returns every card in the game along with some miscellaneous info gathered by the host website that is especially 
#helpful for tracking community interest in a card amongst other things

In [17]:
cards['data']

#examining the data

[{'id': 34541863,
  'name': '"A" Cell Breeding Device',
  'type': 'Spell Card',
  'desc': 'During each of your Standby Phases, put 1 A-Counter on 1 face-up monster your opponent controls.',
  'race': 'Continuous',
  'archetype': 'Alien',
  'card_sets': [{'set_name': 'Force of the Breaker',
    'set_code': 'FOTB-EN043',
    'set_rarity': 'Common',
    'set_rarity_code': '(C)',
    'set_price': '1.58'}],
  'card_images': [{'id': 34541863,
    'image_url': 'https://storage.googleapis.com/ygoprodeck.com/pics/34541863.jpg',
    'image_url_small': 'https://storage.googleapis.com/ygoprodeck.com/pics_small/34541863.jpg'}],
  'card_prices': [{'cardmarket_price': '0.15',
    'tcgplayer_price': '0.22',
    'ebay_price': '4.99',
    'amazon_price': '3.94',
    'coolstuffinc_price': '0.25'}],
  'misc_info': [{'beta_name': 'A Cell Breeding Device',
    'views': 258334,
    'viewsweek': 200,
    'upvotes': 93,
    'downvotes': 87,
    'formats': ['Duel Links', 'TCG', 'OCG'],
    'tcg_date': '2007-05-

In [18]:
len(cards['data'])

#this is in theory every card in the entirety of yugioh complete with additional info such as prices
#NB that this subcategorises different printings of each card meaning the actual number of datapoints is potentially even 
#higher

11743

In [79]:
cards['data'][9]

#NB that the data available varies from card to card and we'll need to further consult the API docs for what info we want to
#store
#for has_effect 1 means that the desc is an effect, 0 means that it is just a description

{'id': 11714098,
 'name': '30,000-Year White Turtle',
 'type': 'Normal Monster',
 'desc': 'A huge turtle that has existed for more than 30,000 years.',
 'atk': 1250,
 'def': 2100,
 'level': 5,
 'race': 'Aqua',
 'attribute': 'WATER',
 'card_images': [{'id': 11714098,
   'image_url': 'https://storage.googleapis.com/ygoprodeck.com/pics/11714098.jpg',
   'image_url_small': 'https://storage.googleapis.com/ygoprodeck.com/pics_small/11714098.jpg'}],
 'card_prices': [{'cardmarket_price': '0.00',
   'tcgplayer_price': '0.00',
   'ebay_price': '10.00',
   'amazon_price': '0.50',
   'coolstuffinc_price': '0.00'}],
 'misc_info': [{'views': 139162,
   'viewsweek': 19,
   'upvotes': 31,
   'downvotes': 15,
   'formats': ['OCG GOAT', 'Duel Links', 'OCG'],
   'ocg_date': '1999-10-17'}]}

In [80]:
Name = []
Kind = []
Attribute = []
Type = []
Level = []
Description = []
Effect = []
ATK = []
DEF = []
Prints = []
Release = []
Formats = []
Views = []
RecentViews = []
LowestPrice = []
Scale = []
LinkRating = []
LinkMarkers = []
Sets = []
SetCodes = []
SetRarities = []
RarityCodes = []
Archetype = []

for i in cards['data']:
    
    Name.append(i['name'])
    
    Kind.append(i['type'])
    
    try:
        Attribute.append(i['attribute'])
    except:
        Attribute.append(None)
        
    Type.append(i['race'])
    
    try:
        Level.append(i['level'])
    except:
        Level.append(None)
        
    Description.append(i['desc'])
    
    try:
        Effect.append(i['misc_info'][0]['has_effect'])
    except:
        Effect.append(None)
    
    try:
        ATK.append(i['atk'])
    except:
        ATK.append(None)
        
    try:
        DEF.append(i['def'])
    except:
        DEF.append(None)
        
    try:
        Scale.append(i['scale'])
    except:
        Scale.append(None)
        
    try:
        LinkRating.append(i['linkval'])
    except:
        LinkRating.append(None)
        
    try:
        LinkMarkers.append(i['linkmarkers'])
    except:
        LinkMarkers.append(None)
        
    try:
        Prints.append(len(i['card_sets']))
    except:
        Prints.append(None)
        
    try:
        Release.append(i['misc_info'][0]['tcg_date'])
    except:
        Release.append(None)
        
    try:
        Formats.append(i['misc_info'][0]['formats'])
    except:
        Formats.append(None)
        
    Views.append(i['misc_info'][0]['views'])
    
    RecentViews.append(i['misc_info'][0]['viewsweek'])
    
    LowestPrice.append(i['card_prices'][0]['tcgplayer_price'])
    
    try:
        Archetype.append(i['archetype'])
    except:
        Archetype.append(None)
        
    sets = []
    setcodes = []
    setrarities = []
    raritycodes = []
    try:
        for x in i['card_sets']:
            sets.append(x['set_name'])
            setcodes.append(x['set_code'])
            setrarities.append(x['set_rarity'])
            raritycodes.append(x['set_rarity_code'])
        Sets.append(sets)
        SetCodes.append(setcodes)
        SetRarities.append(setrarities)
        RarityCodes.append(raritycodes)
    except:
        Sets.append(None)
        SetCodes.append(None)
        SetRarities.append(None)
        RarityCodes.append(None)
    

    
ygo_cards = pd.DataFrame({'name':Name,
                        'kind':Kind,
                        'attribute':Attribute,
                        'type':Type,
                        'level':Level,
                        'card_text':Description,
                        'effect_or_flavour_text':Effect,
                        'attack':ATK,
                        'defence':DEF,
                        'pendulum_scale':Scale,
                        'link_rating':LinkRating,
                        'link_markers':LinkMarkers,
                        'archetype':Archetype,
                        'printings':Prints,
                        'sets':Sets,
                        'set_codes':SetCodes,
                        'set_rarities':SetRarities,
                        'rarity_codes':RarityCodes,
                        'total_views':Views,
                        'views_past_week':RecentViews,
                        'lowest_price':LowestPrice,
                        'release_date':Release,
                        'playable_formats':Formats})

#this creates a dataframe from the main data we have pulled and uses try and except for cases where entries are either 
#missing or for an aspect that not every card possesses e.g. Attribute

In [81]:
ygo_cards

#we can now examine our created dataframe

name            kind attribute        type  \
0           "A" Cell Breeding Device      Spell Card      None  Continuous   
1                 "A" Cell Incubator      Spell Card      None  Continuous   
2      "A" Cell Recombination Device      Spell Card      None  Quick-Play   
3             "A" Cell Scatter Burst      Spell Card      None  Quick-Play   
4       "Infernoble Arms - Durendal"      Spell Card      None       Equip   
...                              ...             ...       ...         ...   
11738             ZW - Sleipnir Mail  Effect Monster     LIGHT       Beast   
11739              ZW - Sylphid Wing  Effect Monster     LIGHT       Beast   
11740           ZW - Tornado Bringer  Effect Monster      WIND      Dragon   
11741           ZW - Ultimate Shield  Effect Monster     EARTH        Aqua   
11742             ZW - Unicorn Spear  Effect Monster     LIGHT       Beast   

       level                                          card_text  \
0        NaN  During each of your Standby Phases, put 1 A-Co...   
1        NaN  Each time an A-Counter(s) is removed from play...   
2        NaN  Target 1 face-up monster on the field; send 1 ...   
3        NaN  Select 1 face-up "Alien" monster you control. ...   
4        NaN  While this card is equipped to a monster: You ...   
...      ...                                                ...   
11738    4.0  You can target 1 "Utopia" monster you control;...   
11739    4.0  You can only control 1 "ZW - Sylphid Wing". Yo...   
11740    5.0  You can target 1 "Utopia" monster you control;...   
11741    4.0  When this card is Normal or Special Summoned: ...   
11742    4.0  You can target 1 "Number C39: Utopia Ray" you ...   

       effect_or_flavour_text  attack  defence  pendulum_scale  ...  \
0                         1.0     NaN      NaN             NaN  ...   
1                         1.0     NaN      NaN             NaN  ...   
2                         1.0     NaN      NaN             NaN  ...   
3                         1.0     NaN      NaN             NaN  ...   
4                         1.0     NaN      NaN             NaN  ...   
...                       ...     ...      ...             ...  ...   
11738                     1.0  1000.0   1000.0             NaN  ...   
11739                     1.0   800.0   1600.0             NaN  ...   
11740                     1.0  1300.0   1800.0             NaN  ...   
11741                     1.0     0.0   2000.0             NaN  ...   
11742                     1.0  1900.0      0.0             NaN  ...   

       printings                                               sets  \
0            1.0                             [Force of the Breaker]   
1            1.0                              [Gladiator's Assault]   
2            1.0                              [Invasion: Vengeance]   
3            1.0                                   [Strike of Neos]   
4            2.0  [2021 Tin of Ancient Battles, Rise of the Duel...   
...          ...                                                ...   
11738        1.0                                    [Primal Origin]   
11739        1.0                               [Brothers of Legend]   
11740        2.0                       [Cosmo Blazer, King's Court]   
11741        2.0                       [Cosmo Blazer, King's Court]   
11742        4.0  [Order of Chaos, Star Pack 2014, Star Pack 201...   

                                              set_codes  \
0                                          [FOTB-EN043]   
1                                          [GLAS-EN062]   
2                                          [INOV-EN063]   
3                                          [STON-EN041]   
4                              [MP21-EN136, ROTD-EN053]   
...                                                 ...   
11738                                      [PRIO-EN096]   
11739                                      [BROL-EN025]   
11740                          [CBLZ-EN006, KICO-EN03

In [82]:
ygo_cards.to_csv("ygocardsbase.csv", index=False, encoding='utf-8')

#as everything seems to be in order, now is a good time to save this dataframe so that we are not constantly accessing the 
#API and worried about making mistakes

In [2]:
req = requests.get('https://db.ygoprodeck.com/api/v7/cardinfo.php?staple=yes')

cards2 = req.json()

#here we can acquire some supplementary information from the database about whether its users consider a card a staple (i.e.
#something that is good enough to be played very often), this is just a nice way of obtaining more domain knowledge and may
#be useful in the modelling

In [3]:
cards2

#checking the data obtained

{'data': [{'id': 86066372,
   'name': 'Accesscode Talker',
   'type': 'Link Monster',
   'desc': '2+ Effect Monsters\r\nYour opponent cannot activate cards or effects in response to this card\'s effect activations. If this card is Link Summoned: You can target 1 Link Monster that was used as material for its Link Summon; this card gains ATK equal to that monster\'s Link Rating x 1000. You can banish 1 Link Monster from your field or GY; destroy 1 card your opponent controls, also for the rest of this turn, you cannot banish monsters with that same Attribute to activate this effect of "Accesscode Talker".',
   'atk': 2300,
   'race': 'Cyberse',
   'attribute': 'DARK',
   'archetype': 'Code Talker',
   'linkval': 4,
   'linkmarkers': ['Top', 'Left', 'Bottom', 'Right'],
   'card_sets': [{'set_name': 'Eternity Code',
     'set_code': 'ETCO-EN046',
     'set_rarity': 'Secret Rare',
     'set_rarity_code': '(ScR)',
     'set_price': '143.55'},
    {'set_name': 'Maximum Gold: El Dorado',
    

In [5]:
len(cards2['data'])

#though there are only a few of these staples versus our complete dataframe it doesn't seem a bad idea to try and gather as
#many features as possible at this point in time

64

In [10]:
CardName = []
Staple = []

for i in cards2['data']:
    CardName.append(i['name'])
    Staple.append(1)
    
ygo_staples = pd.DataFrame({'name':CardName,
                           'staple':Staple})

#creating a dataframe from the staples data NB that most of the other meta data is already stored in our main dataframe

In [11]:
ygo_staples

#checking our stapes dataframe

name  staple
0                       Accesscode Talker       1
1                    Anti-Spell Fragrance       1
2           Apollousa, Bow of the Goddess       1
3             Ash Blossom & Joyous Spring       1
4                        Borreload Dragon       1
..                                    ...     ...
59  The Winged Dragon of Ra - Sphere Mode       1
60                  Triple Tactics Talent       1
61                          Twin Twisters       1
62                         Upstart Goblin       1
63                World Legacy Succession       1

[64 rows x 2 columns]

In [7]:
re = requests.get('https://db.ygoprodeck.com/api/v7/cardinfo.php?banlist=tcg')

cards3 = re.json()

#the other interesting domain knowledge that we can acquire is every card's ban status, this will likely be useful because 
#if a card is unplayable then logically it should not be as valueable

In [8]:
cards3

#examining the data pulled

{'data': [{'id': 8949584,
   'name': 'A Hero Lives',
   'type': 'Spell Card',
   'desc': 'If you control no face-up monsters: Pay half your LP; Special Summon 1 Level 4 or lower "Elemental HERO" monster from your Deck.',
   'race': 'Normal',
   'archetype': 'Elemental HERO',
   'card_sets': [{'set_name': 'Duelist Saga',
     'set_code': 'DUSA-EN087',
     'set_rarity': 'Ultra Rare',
     'set_rarity_code': '(UR)',
     'set_price': '5.07'},
    {'set_name': 'Generation Force',
     'set_code': 'GENF-EN098',
     'set_rarity': 'Ultimate Rare',
     'set_rarity_code': '(UtR)',
     'set_price': '67.58'},
    {'set_name': 'Generation Force',
     'set_code': 'GENF-EN098',
     'set_rarity': 'Ultra Rare',
     'set_rarity_code': '(UR)',
     'set_price': '4.96'},
    {'set_name': 'HERO Strike Structure Deck',
     'set_code': 'SDHS-EN026',
     'set_rarity': 'Common',
     'set_rarity_code': '(C)',
     'set_price': '1.86'},
    {'set_name': 'Legendary Duelists: Magical Hero',
     'set_co

In [9]:
len(cards3['data'])

#essentially the same scenario as for staples here

190

In [13]:
CardNames = []
Ban = []

for i in cards3['data']:
    CardNames.append(i['name'])
    Ban.append(i['banlist_info']['ban_tcg'])
    
ygo_banned = pd.DataFrame({'name':CardNames,
                           'ban_status':Ban})

#creating the ban status dataframe

In [68]:
ygo = pd.read_csv("ygocardsbase.csv")

#importing back in our primary dataframe

In [119]:
ygo = ygo.merge(ygo_staples, how='outer')

#outer merges for the dataframes will align all our data correctly and not create any redundant entries

In [121]:
ygo = ygo.merge(ygo_banned, how='outer')

In [125]:
ygo['staple'].replace({np.nan:0},inplace=True)

#we need to set values in the new columns for cards that have not already been assigned them, staples naturally becomes a
#binary variable

In [126]:
ygo.staple.value_counts()

#if a card is considered a staple by the community behind the API then the value returned is 1 otherwise it is 0, naturally
#only a very small proportion of the cards can be considered staples

0.0    11679
1.0       64
Name: staple, dtype: int64

In [131]:
ygo['ban_status'].replace({np.nan:3,'Semi-Limited':2,'Limited':1,'Banned':0},inplace=True)

#this makes the ban status a categorical variable (explained below why this is the approach)

In [132]:
ygo.ban_status.value_counts()

#the maximum number of copies of a card that can be played by a player is 3 therefore all cards with no restrictions return
#3, semi-limited means only 2, limited means 1 and banned means that card is banned from play i.e. 0 copies allowed, all 
#these returned values reflect this relationship well

3    11553
0      101
1       83
2        6
Name: ban_status, dtype: int64

In [139]:
ygo.to_csv("ygocardsbase.csv", index=False, encoding='utf-8')

#saving the additional columns added to the database

## Some Very Basic Data Cleaning

In [2]:
ygo = pd.read_csv("ygocardsbase.csv")

#reading back in the data

In [3]:
ygo.info()

#examining the columns for both their datatypes and null values

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11743 entries, 0 to 11742
Data columns (total 25 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   name                    11743 non-null  object 
 1   kind                    11743 non-null  object 
 2   attribute               7715 non-null   object 
 3   type                    11743 non-null  object 
 4   level                   7365 non-null   float64
 5   card_text               11743 non-null  object 
 6   effect_or_flavour_text  10974 non-null  float64
 7   attack                  7715 non-null   float64
 8   defence                 7365 non-null   float64
 9   pendulum_scale          296 non-null    float64
 10  link_rating             350 non-null    float64
 11  link_markers            350 non-null    object 
 12  archetype               6631 non-null   object 
 13  printings               11256 non-null  float64
 14  sets                    11256 non-null

In [4]:
ygo.drop_duplicates()

#fortunately we have no duplicates at present

name            kind attribute        type  \
0           "A" Cell Breeding Device      Spell Card       NaN  Continuous   
1                 "A" Cell Incubator      Spell Card       NaN  Continuous   
2      "A" Cell Recombination Device      Spell Card       NaN  Quick-Play   
3             "A" Cell Scatter Burst      Spell Card       NaN  Quick-Play   
4       "Infernoble Arms - Durendal"      Spell Card       NaN       Equip   
...                              ...             ...       ...         ...   
11738             ZW - Sleipnir Mail  Effect Monster     LIGHT       Beast   
11739              ZW - Sylphid Wing  Effect Monster     LIGHT       Beast   
11740           ZW - Tornado Bringer  Effect Monster      WIND      Dragon   
11741           ZW - Ultimate Shield  Effect Monster     EARTH        Aqua   
11742             ZW - Unicorn Spear  Effect Monster     LIGHT       Beast   

       level                                          card_text  \
0        NaN  During each of your Standby Phases, put 1 A-Co...   
1        NaN  Each time an A-Counter(s) is removed from play...   
2        NaN  Target 1 face-up monster on the field; send 1 ...   
3        NaN  Select 1 face-up "Alien" monster you control. ...   
4        NaN  While this card is equipped to a monster: You ...   
...      ...                                                ...   
11738    4.0  You can target 1 "Utopia" monster you control;...   
11739    4.0  You can only control 1 "ZW - Sylphid Wing". Yo...   
11740    5.0  You can target 1 "Utopia" monster you control;...   
11741    4.0  When this card is Normal or Special Summoned: ...   
11742    4.0  You can target 1 "Number C39: Utopia Ray" you ...   

       effect_or_flavour_text  attack  defence  pendulum_scale  ...  \
0                         1.0     NaN      NaN             NaN  ...   
1                         1.0     NaN      NaN             NaN  ...   
2                         1.0     NaN      NaN             NaN  ...   
3                         1.0     NaN      NaN             NaN  ...   
4                         1.0     NaN      NaN             NaN  ...   
...                       ...     ...      ...             ...  ...   
11738                     1.0  1000.0   1000.0             NaN  ...   
11739                     1.0   800.0   1600.0             NaN  ...   
11740                     1.0  1300.0   1800.0             NaN  ...   
11741                     1.0     0.0   2000.0             NaN  ...   
11742                     1.0  1900.0      0.0             NaN  ...   

                                               set_codes  \
0                                         ['FOTB-EN043']   
1                                         ['GLAS-EN062']   
2                                         ['INOV-EN063']   
3                                         ['STON-EN041']   
4                           ['MP21-EN136', 'ROTD-EN053']   
...                                                  ...   
11738                                     ['PRIO-EN096']   
11739                                     ['BROL-EN025']   
11740                       ['CBLZ-EN006', 'KICO-EN035']   
11741                       ['CBLZ-EN007', 'KICO-EN036']   
11742  ['ORCS-EN005', 'SP14-EN004', 'SP14-EN004', 'YS...   

                                        set_rarities  \
0                                         ['Common']   
1                                         ['Common']   
2                                         ['Common']   
3                                         ['Common']   
4                       ['Super Rare', 'Ultra Rare']   
...                                              ...   
11738                                     ['Common']   
11739                                 ['Ultra Rare']   
11740                               ['Rare', 'Rare']   
11741                             ['Common', 'Rare']   
11742  ['Rare', 'Common', 'Starfoil Rare', 'Common']   

                         rarity_codes  tota

In [5]:
ygo.drop(ygo[ygo.printings.isna()].index, inplace=True)

#dropping all rows where there are no listed printings of the card, the majority of these are cards that will be released in
#future sets or promos that were only released in Japan, as a result they are not of interest to this project's goals and in
#particular since they don't have any set codes it will be hard to source prices for them

In [6]:
ygo.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11256 entries, 0 to 11742
Data columns (total 25 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   name                    11256 non-null  object 
 1   kind                    11256 non-null  object 
 2   attribute               7307 non-null   object 
 3   type                    11256 non-null  object 
 4   level                   6970 non-null   float64
 5   card_text               11256 non-null  object 
 6   effect_or_flavour_text  10644 non-null  float64
 7   attack                  7307 non-null   float64
 8   defence                 6970 non-null   float64
 9   pendulum_scale          281 non-null    float64
 10  link_rating             337 non-null    float64
 11  link_markers            337 non-null    object 
 12  archetype               6437 non-null   object 
 13  printings               11256 non-null  float64
 14  sets                    11256 non-null

In [7]:
ygo.dropna(subset=['release_date'],inplace=True)

#there are some cards in our data from upcoming sets that haven't yet been released outside of Japan therefore we should 
#remove them 

In [8]:
ygo.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11165 entries, 0 to 11742
Data columns (total 25 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   name                    11165 non-null  object 
 1   kind                    11165 non-null  object 
 2   attribute               7248 non-null   object 
 3   type                    11165 non-null  object 
 4   level                   6916 non-null   float64
 5   card_text               11165 non-null  object 
 6   effect_or_flavour_text  10554 non-null  float64
 7   attack                  7248 non-null   float64
 8   defence                 6916 non-null   float64
 9   pendulum_scale          278 non-null    float64
 10  link_rating             332 non-null    float64
 11  link_markers            332 non-null    object 
 12  archetype               6370 non-null   object 
 13  printings               11165 non-null  float64
 14  sets                    11165 non-null

In [9]:
ygo.archetype.value_counts()[350:]

#fundamentally the data here is not manageable since there can be cards which belong to multiple archetypes and there are
#several archetypes with few cards as well as several cards without an archetype, this is all without considering whether
#the archetypings decided on in the database are accurate, thus we should remove this column for now

Madoor                          4
Aether                          3
Barbaros                        3
Evolzar                         3
Celtic Guard                    3
Deep Sea                        3
Heraldry                        3
Yubel                           3
Apoqliphort                     3
Butterfly                       3
Malicevorous                    3
Fleur                           3
Jester                          3
Sunseed                         3
Dracoverlord                    3
Chaos Phantom                   3
Stigmatika                      2
Synchro                         2
Branded                         2
Cupid                           2
Materiactor                     2
Priestess                       2
Fairy Tail                      2
Cyber                           2
Pendulum Dragon                 2
HERO                            2
Glacial Beast                   2
Lady of Lament                  2
Live☆Twin                       2
Spiritual Art 

In [10]:
ygo = ygo.drop('archetype',axis=1)

In [11]:
ygo.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11165 entries, 0 to 11742
Data columns (total 24 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   name                    11165 non-null  object 
 1   kind                    11165 non-null  object 
 2   attribute               7248 non-null   object 
 3   type                    11165 non-null  object 
 4   level                   6916 non-null   float64
 5   card_text               11165 non-null  object 
 6   effect_or_flavour_text  10554 non-null  float64
 7   attack                  7248 non-null   float64
 8   defence                 6916 non-null   float64
 9   pendulum_scale          278 non-null    float64
 10  link_rating             332 non-null    float64
 11  link_markers            332 non-null    object 
 12  printings               11165 non-null  float64
 13  sets                    11165 non-null  object 
 14  set_codes               11165 non-null

In [12]:
type(ygo.playable_formats[0])
print(ygo.playable_formats[0])

#unfortunately the intended lists of formats have ended up as strings rather than lists of strings so we will have to fix 
#them

['Duel Links', 'TCG', 'OCG']


In [13]:
ygo['playable_formats'] = [x.strip("[]").split(',') for x in ygo.playable_formats]

In [14]:
completefixes = []
for i in ygo.playable_formats:
    fixed =[]
    for x in i:
        fixed.append(x.strip("'' "))
    completefixes.append(fixed)
print(completefixes)

#this cell combined with the one above and below reform the column to what it should be

[['Duel Links', 'TCG', 'OCG'], ['Duel Links', 'TCG', 'OCG'], ['Duel Links', 'TCG', 'OCG'], ['Duel Links', 'TCG', 'OCG'], ['TCG', 'OCG'], ['TCG', 'OCG'], ['TCG', 'OCG'], ['Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Speed Duel', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'Speed Duel', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['Speed Duel', 'Duel Links', 'TCG', 'OCG'], ['GOAT', 'OCG GOAT', 'Duel Links', 'TCG', 'OCG'], ['Duel Links', 'TCG', 'OCG'], ['TCG', 'OCG'], ['GOAT', 'OCG GOA

In [15]:
ygo['playable_formats'] = completefixes

In [16]:
ygo = ygo.explode('playable_formats',ignore_index=True)

#this expands out our fixed column so that we can remove all the non tcg cards from it, we only want tcg cards since the 
#data we are obtaining is only relevant for them
#NB we may have to perform further removal on non-tcg printings of tcg cards later

In [17]:
ygo = ygo[ygo.playable_formats == 'TCG']

In [18]:
ygo = ygo.drop('playable_formats',axis=1)

#at this point we have no further need of the column so we can drop it

In [19]:
ygo.reset_index(drop=True,inplace=True)

In [20]:
ygo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11094 entries, 0 to 11093
Data columns (total 23 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   name                    11094 non-null  object 
 1   kind                    11094 non-null  object 
 2   attribute               7248 non-null   object 
 3   type                    11094 non-null  object 
 4   level                   6916 non-null   float64
 5   card_text               11094 non-null  object 
 6   effect_or_flavour_text  10483 non-null  float64
 7   attack                  7248 non-null   float64
 8   defence                 6916 non-null   float64
 9   pendulum_scale          278 non-null    float64
 10  link_rating             332 non-null    float64
 11  link_markers            332 non-null    object 
 12  printings               11094 non-null  float64
 13  sets                    11094 non-null  object 
 14  set_codes               11094 non-null

In [21]:
ygo[ygo.pendulum_scale.isna() == False][ygo.kind == 'Fusion Monster']

#these two cards are in fact Pendulum Effect Fusion Monster rather than Fusion monsters so we'll fix that, otherwise this
#column is fine to work with

C:\Users\georg\AppData\Local\Temp/ipykernel_13004/1050345024.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  ygo[ygo.pendulum_scale.isna() == False][ygo.kind == 'Fusion Monster']


name            kind attribute     type  level  \
7168  Parametalfoes Azortless  Fusion Monster      FIRE  Psychic    7.0   
9114   Starving Venemy Dragon  Fusion Monster      DARK   Dragon    7.0   

                                              card_text  \
7168  [ Pendulum Effect ] If a face-up "Metalfoes" c...   
9114  [ Pendulum Effect ] Each time a card(s) is sen...   

      effect_or_flavour_text  attack  defence  pendulum_scale  ...  \
7168                     1.0  2500.0   2000.0             8.0  ...   
9114                     1.0  2500.0   2000.0             1.0  ...   

                        sets       set_codes     set_rarities rarity_codes  \
7168      ['Blazing Vortex']  ['BLVO-EN039']   ['Super Rare']     ['(SR)']   
9114  ['Brothers of Legend']  ['BROL-EN034']  ['Secret Rare']    ['(ScR)']   

     total_views views_past_week lowest_price  release_date  staple  \
7168       13336              44         0.13    2021-02-04     0.0   
9114        7893             154         0.23    2021-12-02     0.0   

      ban_status  
7168           3  
9114           3  

[2 rows x 23 columns]

In [22]:
ygo.at[7168,'kind'] = 'Pendulum Effect Fusion Monster'

In [23]:
ygo.at[9114,'kind'] = 'Pendulum Effect Fusion Monster'

In [26]:
ygo.attribute.value_counts()

#while maybe not something that will be useful at present, if image recognition is ever included in this project in the 
#future, it will be worth setting the attribute for spell cards to SPELL and for traps to TRAP

DARK      1984
EARTH     1703
LIGHT     1494
WATER      731
WIND       708
FIRE       623
DIVINE       5
Name: attribute, dtype: int64

In [42]:
ygo.loc[ygo.kind == 'Spell Card', 'attribute'] = 'SPELL'

In [46]:
ygo.loc[ygo.kind == 'Trap Card', 'attribute'] = 'TRAP'

In [49]:
ygo.attribute.value_counts()

SPELL     2168
DARK      1984
EARTH     1703
TRAP      1678
LIGHT     1494
WATER      731
WIND       708
FIRE       623
DIVINE       5
Name: attribute, dtype: int64

In [50]:
ygo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11094 entries, 0 to 11093
Data columns (total 23 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   name                    11094 non-null  object 
 1   kind                    11094 non-null  object 
 2   attribute               11094 non-null  object 
 3   type                    11094 non-null  object 
 4   level                   6916 non-null   float64
 5   card_text               11094 non-null  object 
 6   effect_or_flavour_text  10483 non-null  float64
 7   attack                  7248 non-null   float64
 8   defence                 6916 non-null   float64
 9   pendulum_scale          278 non-null    float64
 10  link_rating             332 non-null    float64
 11  link_markers            332 non-null    object 
 12  printings               11094 non-null  float64
 13  sets                    11094 non-null  object 
 14  set_codes               11094 non-null

In [61]:
ygo[ygo.effect_or_flavour_text == 0]

Empty DataFrame
Columns: [name, kind, attribute, type, level, card_text, effect_or_flavour_text, attack, defence, pendulum_scale, link_rating, link_markers, printings, sets, set_codes, set_rarities, rarity_codes, total_views, views_past_week, lowest_price, release_date, staple, ban_status]
Index: []

[0 rows x 23 columns]

In [72]:
ygo[ygo.effect_or_flavour_text.isna() == True]

#it seems for many monsters without effects rather than having 0 appended to this column, instead I accidentally appended
#None this should be a simple fix

name            kind attribute     type  level  \
11                 7 Colored Fish  Normal Monster     WATER     Fish    4.0   
100                Acrobat Monkey  Normal Monster     EARTH  Machine    3.0   
146                         Aitsu  Normal Monster      FIRE    Fairy    5.0   
160            Alexandrite Dragon  Normal Monster     LIGHT   Dragon    4.0   
174            Alien Shocktrooper  Normal Monster     EARTH  Reptile    4.0   
...                           ...             ...       ...      ...    ...   
11019               Zera the Mant  Ritual Monster      DARK    Fiend    8.0   
11035                         Zoa  Normal Monster      DARK    Fiend    7.0   
11046              Zombie Warrior  Fusion Monster      DARK   Zombie    3.0   
11049                     Zombino  Normal Monster     EARTH   Zombie    4.0   
11080  Zure, Knight of Dark World  Normal Monster      DARK    Fiend    4.0   

                                               card_text  \
11     A rare rainbow fish that has never been caught...   
100    An autonomous monkey type robot which was deve...   
146    He seems to be very unreliable, but he might h...   
160    Many of the czars' lost jewels can be found in...   
174    The Aliens have used a mysterious biological s...   
...                                                  ...   
11019  This card can only be Ritual Summoned with the...   
11035  A monster whose full potential can be achieved...   
11046                 "Skull Servant" + "Battle Warrior"   
11049  The two are so close\r\nThey die and return to...   
11080  The name of this illustrious knight is known b...   

       effect_or_flavour_text  attack  defence  pendulum_scale  ...  \
11                        NaN  1800.0    800.0             NaN  ...   
100                       NaN  1000.0   1800.0             NaN  ...   
146                       NaN   100.0    100.0             NaN  ...   
160                       NaN  2000.0    100.0             NaN  ...   
174                       NaN  1900.0    800.0             NaN  ...   
...                       ...     ...      ...             ...  ...   
11019                     NaN  2800.0   2300.0             NaN  ...   
11035                     NaN  2600.0   1900.0             NaN  ...   
11046                     NaN  1200.0    900.0             NaN  ...   
11049                     NaN  2000.0      0.0             NaN  ...   
11080                     NaN  1800.0   1500.0             NaN  ...   

                                                    sets  \
11     ['Gold Series', 'Metal Raiders', 'Metal Raider...   
100    ['Dark Crisis', 'Dark Crisis', 'Dark Revelatio...   
146     ['Dark Revelation Volume 1', "Magician's Force"]   
160    ['2-Player Starter Deck: Yuya & Declan', 'Batt...   
174                               ['Tactical Evolution']   
...                                                  ...   
11019       ['Premium Pack (TCG)', 'Premium Pack (TCG)']   
11035  ["Legendary Collection 4: Joey's World Mega Pa...   
11046                          ['OTS Tournament Pack 1']   
11049       ['2018 Mega-Tin Mega Pack', 'Extreme Force']   
11080  ['Dark Revelation Volume 4', 'Elemental Energy...   

                                               set_codes  \
11     ['GLD1-EN001', 'MRD-098', 'MRD-E098', 'MRD-EN0...   
100    ['DCR-003', 'DCR-EN003', 'DR1-EN165', 'YSDS-EN...   
146                             ['DR1-EN111', 'MFC-056']   
160    ['YS15-ENY01', 'BP02-EN004', 'BP02-EN004', 'LD...   
174                                       ['TAEV-EN001']   
...                                                  ...   
11019                       ['PP01-EN011', 'PP01-EN011']   
11035  ['LCJW-EN173', 'PT1-EN001', 'WP11-EN011', 'TFK...   
11046                                     ['OP01-EN019']   
11049                       ['MP18-EN169', 'EXFO-EN001']   
11080  ['DR04-EN061', 'EEN-EN001', 'SDGU-EN004', 'YSD...   

                                            set_rarities  \
11  

In [73]:
ygo.loc[ygo.effect_or_flavour_text.isna() == True, 'effect_or_flavour_text'] = 0

In [75]:
ygo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11094 entries, 0 to 11093
Data columns (total 23 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   name                    11094 non-null  object 
 1   kind                    11094 non-null  object 
 2   attribute               11094 non-null  object 
 3   type                    11094 non-null  object 
 4   level                   6916 non-null   float64
 5   card_text               11094 non-null  object 
 6   effect_or_flavour_text  11094 non-null  float64
 7   attack                  7248 non-null   float64
 8   defence                 6916 non-null   float64
 9   pendulum_scale          278 non-null    float64
 10  link_rating             332 non-null    float64
 11  link_markers            332 non-null    object 
 12  printings               11094 non-null  float64
 13  sets                    11094 non-null  object 
 14  set_codes               11094 non-null

In [83]:
ygo.to_csv("ygocardsbase.csv", index=False, encoding='utf-8')

#saving our updated database so that it is now the master database from which we can work

## Examining a Potential Future Issue

There remain a few columns which are lists but upon being imported as a csv the lists become strings, these columns will always have to be cleaned whenever we use the csv and it is worth checking how big our dataset is overall now when these columns get expanded out.

In [84]:
ygo = pd.read_csv("ygocardsbase.csv")

In [85]:
ygo['sets'] = [x.strip("[]").split(',') for x in ygo.sets]
completefixes = []
for i in ygo.sets:
    fixed =[]
    for x in i:
        fixed.append(x.strip("'' "))
    completefixes.append(fixed)
print(completefixes)
ygo['sets'] = completefixes

#this code is for the most part the same as what we have used earlier to clean up the list columns that get stored as 
#strings

[['Force of the Breaker'], ['"Gladiator\'s Assault"'], ['Invasion: Vengeance'], ['Strike of Neos'], ['2021 Tin of Ancient Battles', 'Rise of the Duelist'], ['2021 Tin of Ancient Battles', 'Rise of the Duelist'], ['2021 Tin of Ancient Battles', 'Rise of the Duelist'], ['2015 Mega-Tin Mega Pack', 'The New Challengers', 'The New Challengers: Super Edition'], ['Ancient Sanctuary', 'Dark Revelation Volume 2'], ['Dark Beginning 1', '"Pharaoh\'s Servant"', '"Pharaoh\'s Servant"', '"Pharaoh\'s Servant"', 'Retro Pack 2', 'Starter Deck: Yugi Reloaded'], ['Ancient Sanctuary', 'Dark Revelation Volume 2'], ['Gold Series', 'Metal Raiders', 'Metal Raiders', 'Metal Raiders', 'Starter Deck: Joey', 'Structure Deck: Fury from the Deep'], ['Battle Pack 3: Monster League', 'Battle Pack 3: Monster League', 'Duel Terminal 2', '"Pharaoh\'s Servant"', '"Pharaoh\'s Servant"', '"Pharaoh\'s Servant"', 'Speed Duel: Scars of Battle'], ['Gold Series', 'Pharaonic Guardian'], ['Dark Revelation Volume 1', 'Pharaonic Gu

In [93]:
ygo['sets']

0                                   [Force of the Breaker]
1                                  ["Gladiator's Assault"]
2                                    [Invasion: Vengeance]
3                                         [Strike of Neos]
4        [2021 Tin of Ancient Battles, Rise of the Duel...
                               ...                        
11089                                      [Primal Origin]
11090                                 [Brothers of Legend]
11091                       [Cosmo Blazer, "King's Court"]
11092                       [Cosmo Blazer, "King's Court"]
11093    [Order of Chaos, Star Pack 2014, Star Pack 201...
Name: sets, Length: 11094, dtype: object

In [94]:
ygo['set_codes'] = [x.strip("[]").split(',') for x in ygo.set_codes]
completefixes = []
for i in ygo.set_codes:
    fixed =[]
    for x in i:
        fixed.append(x.strip("'' "))
    completefixes.append(fixed)
print(completefixes)
ygo['set_codes'] = completefixes

[['FOTB-EN043'], ['GLAS-EN062'], ['INOV-EN063'], ['STON-EN041'], ['MP21-EN136', 'ROTD-EN053'], ['MP21-EN137', 'ROTD-EN054'], ['MP21-EN138', 'ROTD-EN055'], ['MP15-EN169', 'NECH-EN059', 'NECH-ENS10'], ['AST-070', 'DR2-EN183'], ['DB1-EN198', 'PSV-088', 'PSV-E088', 'PSV-EN088', 'RP02-EN022', 'YSYR-EN010'], ['AST-091', 'DR2-EN204'], ['GLD1-EN001', 'MRD-098', 'MRD-E098', 'MRD-EN098', 'SDJ-008', 'SD4-EN002'], ['BP03-EN135', 'BP03-EN135', 'DT02-EN038', 'PSV-004', 'PSV-E004', 'PSV-EN004', 'SBSC-EN029'], ['GLD1-EN007', 'PGD-024'], ['DR1-EN018', 'PGD-070', 'SS01-ENB11'], ['DCR-030', 'DCR-EN030', 'DR1-EN192', 'LCJW-EN241'], ['CP03-EN018', 'DR3-EN157', 'FET-EN037', 'FET-EN037', 'LCYW-EN280', 'LEHD-ENA26', 'YSDS-EN029'], ['LOD-032', 'LOD-EN032'], ['BP02-EN179', 'BP02-EN179', 'DR2-EN105', 'DT02-EN048', 'DP1-EN025', 'IOC-104', 'IOC-EN104', 'YS14-EN036'], ['DUSA-EN087', 'GENF-EN098', 'GENF-EN098', 'SDHS-EN026', 'LED6-EN022'], ['DB2-EN187', 'HL1-EN003', 'LOD-078', 'LOD-EN078', 'LEDU-EN021', 'LDS1-EN029'

In [95]:
ygo['set_codes']

0                                            [FOTB-EN043]
1                                            [GLAS-EN062]
2                                            [INOV-EN063]
3                                            [STON-EN041]
4                                [MP21-EN136, ROTD-EN053]
                               ...                       
11089                                        [PRIO-EN096]
11090                                        [BROL-EN025]
11091                            [CBLZ-EN006, KICO-EN035]
11092                            [CBLZ-EN007, KICO-EN036]
11093    [ORCS-EN005, SP14-EN004, SP14-EN004, YS13-EN018]
Name: set_codes, Length: 11094, dtype: object

In [96]:
ygo['set_rarities'] = [x.strip("[]").split(',') for x in ygo.set_rarities]
completefixes = []
for i in ygo.set_rarities:
    fixed =[]
    for x in i:
        fixed.append(x.strip("'' "))
    completefixes.append(fixed)
print(completefixes)
ygo['set_rarities'] = completefixes

[['Common'], ['Common'], ['Common'], ['Common'], ['Super Rare', 'Ultra Rare'], ['Super Rare', 'Common'], ['Super Rare', 'Super Rare'], ['Super Rare', 'Super Rare', 'Super Rare'], ['Common', 'Common'], ['Common', 'Common', 'Common', 'Common', 'Common', 'Common'], ['Short Print', 'Common'], ['Common', 'Common', 'Common', 'Common', 'Common', 'Common'], ['Common', 'Shatterfoil Rare', 'Duel Terminal Normal Parallel Rare', 'Common', 'Common', 'Common', 'Common'], ['Common', 'Common'], ['Common', 'Common', 'Common'], ['Common', 'Common', 'Common', 'Rare'], ['Common', 'Super Rare', 'Super Rare', 'Ultimate Rare', 'Secret Rare', 'Common', 'Common'], ['Common', 'Common'], ['Common', 'Mosaic Rare', 'Common', 'Duel Terminal Normal Parallel Rare', 'Common', 'Common', 'Common', 'Common'], ['Ultra Rare', 'Ultimate Rare', 'Ultra Rare', 'Common', 'Common'], ['Common', 'Common', 'Common', 'Common', 'Common', 'Common', 'Common', 'Common', 'Common'], ['Short Print', 'Common'], ['Common', 'Common'], ['Commo

In [97]:
ygo['set_rarities']

0                                     [Common]
1                                     [Common]
2                                     [Common]
3                                     [Common]
4                     [Super Rare, Ultra Rare]
                         ...                  
11089                                 [Common]
11090                             [Ultra Rare]
11091                             [Rare, Rare]
11092                           [Common, Rare]
11093    [Rare, Common, Starfoil Rare, Common]
Name: set_rarities, Length: 11094, dtype: object

In [98]:
ygo['rarity_codes'] = [x.strip("[]").split(',') for x in ygo.rarity_codes]
completefixes = []
for i in ygo.rarity_codes:
    fixed =[]
    for x in i:
        fixed.append(x.strip("'' "))
    completefixes.append(fixed)
print(completefixes)
ygo['rarity_codes'] = completefixes

[['(C)'], ['(C)'], ['(C)'], ['(C)'], ['(SR)', '(UR)'], ['(SR)', '(C)'], ['(SR)', '(SR)'], ['(SR)', '(SR)', '(SR)'], ['(C)', '(C)'], ['(C)', '(C)', '(C)', '(C)', '(C)', '(C)'], ['(SP)', '(C)'], ['(C)', '(C)', '(C)', '(C)', '(C)', '(C)'], ['(C)', '(SHR)', '(DNPR)', '(C)', '(C)', '(C)', '(C)'], ['(C)', '(C)'], ['(C)', '(C)', '(C)'], ['(C)', '(C)', '(C)', '(R)'], ['(C)', '(SR)', '(SR)', '(UtR)', '(ScR)', '(C)', '(C)'], ['(C)', '(C)'], ['(C)', '(MSR)', '(C)', '(DNPR)', '(C)', '(C)', '(C)', '(C)'], ['(UR)', '(UtR)', '(UR)', '(C)', '(C)'], ['(C)', '(C)', '(C)', '(C)', '(C)', '(C)', '(C)', '(C)', '(C)'], ['(SP)', '(C)'], ['(C)', '(C)'], ['(C)', '(C)'], ['(ScR)', '(R)', '(ScR)'], ['(C)', '(C)', '(C)', '(C)', '(C)', '(C)', '(C)'], ['(ScR)', '(SR)'], ['(R)', '(R)', '(UtR)'], ['(UR)'], ['(C)'], ['(UR)', '(SR)'], ['(C)', '(R)'], ['(C)'], ['(C)', '(C)'], ['(C)', '(C)'], ['(UR)'], ['(C)', '(R)'], ['(C)', '(C)'], ['(C)', '(C)', '(C)', '(C)'], ['(C)', '(C)'], ['(C)', '(C)'], ['(ScR)', '(SR)', '(SR)', '

In [99]:
ygo['rarity_codes']

0                         [(C)]
1                         [(C)]
2                         [(C)]
3                         [(C)]
4                  [(SR), (UR)]
                  ...          
11089                     [(C)]
11090                    [(UR)]
11091                [(R), (R)]
11092                [(C), (R)]
11093    [(R), (C), (SFR), (C)]
Name: rarity_codes, Length: 11094, dtype: object

In [103]:
ygo.explode('rarity_codes')

#from the looks of things we have 31081 when we explode the sets column but 31042 when we explode the other 3 that partner
#it, as a result we will probably when using these columns focus on exploding the other three and rejoining the exploded
#dataframes together with either merge or join, for now we'll keep the dataframe saved in its unexploded format to make
#storing it smaller
#NB the most important of these columns should be set_codes anyway

name            kind attribute        type  \
0           "A" Cell Breeding Device      Spell Card     SPELL  Continuous   
1                 "A" Cell Incubator      Spell Card     SPELL  Continuous   
2      "A" Cell Recombination Device      Spell Card     SPELL  Quick-Play   
3             "A" Cell Scatter Burst      Spell Card     SPELL  Quick-Play   
4       "Infernoble Arms - Durendal"      Spell Card     SPELL       Equip   
...                              ...             ...       ...         ...   
11092           ZW - Ultimate Shield  Effect Monster     EARTH        Aqua   
11093             ZW - Unicorn Spear  Effect Monster     LIGHT       Beast   
11093             ZW - Unicorn Spear  Effect Monster     LIGHT       Beast   
11093             ZW - Unicorn Spear  Effect Monster     LIGHT       Beast   
11093             ZW - Unicorn Spear  Effect Monster     LIGHT       Beast   

       level                                          card_text  \
0        NaN  During each of your Standby Phases, put 1 A-Co...   
1        NaN  Each time an A-Counter(s) is removed from play...   
2        NaN  Target 1 face-up monster on the field; send 1 ...   
3        NaN  Select 1 face-up "Alien" monster you control. ...   
4        NaN  While this card is equipped to a monster: You ...   
...      ...                                                ...   
11092    4.0  When this card is Normal or Special Summoned: ...   
11093    4.0  You can target 1 "Number C39: Utopia Ray" you ...   
11093    4.0  You can target 1 "Number C39: Utopia Ray" you ...   
11093    4.0  You can target 1 "Number C39: Utopia Ray" you ...   
11093    4.0  You can target 1 "Number C39: Utopia Ray" you ...   

       effect_or_flavour_text  attack  defence  pendulum_scale  ...  \
0                         1.0     NaN      NaN             NaN  ...   
1                         1.0     NaN      NaN             NaN  ...   
2                         1.0     NaN      NaN             NaN  ...   
3                         1.0     NaN      NaN             NaN  ...   
4                         1.0     NaN      NaN             NaN  ...   
...                       ...     ...      ...             ...  ...   
11092                     1.0     0.0   2000.0             NaN  ...   
11093                     1.0  1900.0      0.0             NaN  ...   
11093                     1.0  1900.0      0.0             NaN  ...   
11093                     1.0  1900.0      0.0             NaN  ...   
11093                     1.0  1900.0      0.0             NaN  ...   

                                                    sets  \
0                                 [Force of the Breaker]   
1                                ["Gladiator's Assault"]   
2                                  [Invasion: Vengeance]   
3                                       [Strike of Neos]   
4      [2021 Tin of Ancient Battles, Rise of the Duel...   
...                                                  ...   
11092                     [Cosmo Blazer, "King's Court"]   
11093  [Order of Chaos, Star Pack 2014, Star Pack 201...   
11093  [Order of Chaos, Star Pack 2014, Star Pack 201...   
11093  [Order of Chaos, Star Pack 2014, Star Pack 201...   
11093  [Order of Chaos, Star Pack 2014, Star Pack 201...   

                                              set_codes  \
0                                          [FOTB-EN043]   
1                                          [GLAS-EN062]   
2                                          [INOV-EN063]   
3                                          [STON-EN041]   
4                              [MP21-EN136, ROTD-EN053]   
...                                                 ...   
11092                          [CBLZ-EN007, KICO-EN036]   
11093  [ORCS-EN005, SP14-EN004, SP14-EN004, YS13-EN018]   
11093  [ORCS-EN005, SP14-EN004, SP14-EN004, YS13-EN018]   
11093  [ORCS-EN005, SP14-EN004, SP14-EN004, YS13-EN018]   
11093  [ORCS-EN005, SP14-EN004, SP14-EN004, YS13-EN018]   

       

We should now be ready to begin the proper EDA, data cleaning and feature engineering.